# L3X: Feature engineering for part-of-speech tagging

## Introduction

The system in lab&nbsp;L3 implements a sequence model based on a classifier called **averaged perceptron**. In this model, sentences are tagged left-to-right. The pool of information that the system can tap to tag a word $w$ therefore includes both the word&nbsp;$w$ itself as well as the surrounding words, and moreover information about the tags that the system has already assigned to preceding words. The job of the developer is to extract useful features of the data from this pool. In this lab you will practice this skill and see what effect different features have on the correctness of the system.

The first code cell imports the Python module that is required for this lab.

In [ ]:
import lt3x

We also load the training data and the development data for this lab. These data sets are taken from the German treebank released by the [Universal Dependencies Project](http://universaldependencies.org):

In [ ]:
training_data = lt3x.read_data("/courses/729G17/labs/l3x/data/train.txt")
dev_data = lt3x.read_data("/courses/729G17/labs/l3x/data/dev.txt")

The following code extracts all unique tags from the training data:

In [ ]:
all_tags = set()
for tagged_sentence in training_data:
    for word, tag in tagged_sentence:
        all_tags.add(tag)
all_tags = sorted(all_tags)
print(" ".join(all_tags))

These tags are defined and exemplified in the document [Universal POS Tags](http://universaldependencies.org/u/pos/all.html).

## Background

Before you can start to extract features, it is useful to understand how these features are used by the system. To illustrate this we define a variant of the perceptron tagger that only extracts a single feature, the current word.

In [ ]:
class DemoTagger(lt3x.PerceptronTagger):
    
    def get_features(self, words, i, pred_tags):
        if self.debug:
            print("words: {}".format(" ".join(words)))
            print("i: {} (current word: {})".format(i, words[i]))
            print("pred_tags: {}".format(" ".join(pred_tags)))
            print()
        return [words[i]]

We train this tagger and evaluate it on the development data:

In [ ]:
demo_tagger = DemoTagger(all_tags)
demo_tagger.debug = False
demo_tagger.train(training_data)
demo_matrix = lt3x.confusion_matrix(demo_tagger, dev_data)
print("accuracy = {:.2%}".format(lt3x.accuracy(demo_matrix)))
demo_tagger.debug = True

Which features are extracted is controlled by the method `get_features()`. This method is called once for each word in the sentence that is to be tagged. It takes three arguments: `words` is the list with all words in the sentence, `i` is the position of the current word, and `pred_tags` is the list with the tags that have been predicted so far. The task of the method is to return the features that the system should use to decide which tag the word in position `i` should get. As an example, we show the features that are extracted when the system tags the sentence *Ben liebt Anna* ‘Ben loves Anna’:

In [ ]:
demo_tagger.tag("Ben liebt Anna".split())

How the extracted features are used depends on whether the system is in tagging mode or training mode.

### How features are used during tagging

In a trained system, the features are used to make a decision about which part-of-speech tag the current word should be labelled with. A perceptron tagger consists of a number of perceptrons, one for each tag. Each perceptron $p$ takes the extracted features as its input &ndash; in the demo tagger, each perceptron &lsquo;sees&rsquo; the current word. Each feature $f$ is associated with a corresponding **feature weight**, which can be either positive or negative. This feature weight is specific to $p$ &ndash; a different perceptron may associate the same feature with a different weight. The weights of all extracted features are summed up to yield the perceptron&rsquo;s **activation**. If the weight is positive, then the system will be more inclined to label the current word with the tag that corresponds to&nbsp;$p$; a negative weight has the opposite effect. For example, in the demo tagger we would expect the perceptron for nouns to assign high weights to words such as *Auto* ‘car’ and *Haus* ‘house’, and low weights to *teuer* ‘expensive’ and *alt* ‘old’, whereas for the adjective-perceptron it should be the other way around. That perceptron which yields the highest activation &lsquo;wins&rsquo; and gets to decide the tag for the current word.

### How features are used during training

The goal of training is to set the weights, that is, to learn which features are positively correlated with a given tag, and which features are negatively correlated. The weights are modified using the **perceptron learning rule**, which says that the weights for all extracted features $f$ should be increased in the perceptron that corresponds to the gold-standard tag, and decreased in the perceptron that corresponds to the predicted tag. If the system predicts the correct tag, the increase and the decrease cancel out each other, and the weights remain unchanged.

### What features can be extracted?

In the example code above, only the current word is extracted as a feature; but using the data structures that are passed as arguments to `get_features()` you can even extract e.g. the previous word, the next word, or the tag that has been predicted for the previous word. All of these values can be computed based on the arguments `words`, `i`, and `pred_tags`.

### The power of feature combinations

The real power of the multiclass perceptron is in **feature combinations**. Imagine that you want to tag the word *bad* in the Swedish sentence *Jag bad om en kort bit* ‘I asked for a short piece’. The correct tag is &lsquo;verb&rsquo;, but without the preceding *jag* (or some other pronoun), the more likely tag could be &lsquo;noun&rsquo;. How could we resolve this ambiguity? The solution is to distinguish between two features: one for the current word, and one for the combination of the current word and the previous word.

Based on a corpus analysis, we may want the weight of the feature
```
"current_word=bad"
```
to be relatively high in the noun perceptron, and slightly lower in the verb perceptron. However, we could try to make the weight of the complex feature
```
"current_word=bad+previous_word=Jag"
```
strongly *negative* for nouns, and strongly *positive* for verbs. In this way, the activation for &lsquo;noun&rsquo; could be lower than the activation for &lsquo;verb&rsquo;, and thus give us the correct prediction.

The example shows that perceptrons that can use feature combinations are much more powerful than perceptrons with only atomic features. This has to do with a concept known as *linear separability*, which you can learn more about in the background materials for this lab.

## The problem

Here is the problem that you will have to solve:

<div class="panel panel-primary">
<div class="panel-heading">Problem&nbsp;1</div>
<div class="panel-body">
<p>Think about which information could be useful for the system and modify the existing system so that it extracts the corresponding features. Experiment with different combinations of features. The goal is to create a system whose accuracy on the development data is as high as possible.</p>
<p>To get a pass grade on the lab, your system needs to achieve an accuracy of at least&nbsp;87% on the development data. In addition to writing the feature extraction code, you should also provide a short discussion of how you devised your features.</p>
</div>
</div>

To solve this problem, you are supposed to edit the following code cell:

In [ ]:
class OurTagger(lt3x.PerceptronTagger):
    
    def get_features(self, words, i, pred_tags):
        """Extract features for the specified configuration."""
        features = []
        def extract(*args):
            features.append((len(features),) + tuple(args))
        extract(words[i])
        return features

As you can see, the method `get_features()` returns a list of features. To build up this list it uses an auxiliary function `extract()`. You should call this function for every feature that you would like to extract.

The function `extract()` takes an arbitrary number of values, builds a *tuple* from these values, and appends the tuple to the list. This is convenient when you want to use feature combinations. For example, to extract the combination current&nbsp;word + previous&nbsp;word  from above, you could call `extract()` as follows:
```
extract(words[i], words[i-1])
```
(But be careful: You will have to treat the case `i=0` separately, as `words[-1]` means &lsquo;the last element of the list `words`&rsquo; in Python.)

Note that `extract()` implicitly numbers the extracted features, which is useful when you have two features that can take the same value but &lsquo;mean&rsquo; different things. For example, in addition to one atomic feature for the current word you may want to extract a separate atomic feature for the previous word. Without the numbering, the system would not &lsquo;know&rsquo; whether a word such as *bad* happens to be the value of the first or the second feature.

Use the following code to evaluate the tagger:

In [ ]:
our_tagger = OurTagger(all_tags)
our_tagger.train(training_data)
our_tagger_matrix = lt3x.confusion_matrix(our_tagger, dev_data)
print("accuracy = {:.2%}".format(lt3x.accuracy(our_tagger_matrix)))

*TODO: Insert your description of how you devised the features here*